In [1]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import numpy as np
import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)

In [3]:
def cnn_model_fn(features, labels, mode):
    """Model function for CNN."""
    # Input Layer
    # Reshape X to 4-D tensor: [batch_size, width, height, channels]
    # MNIST images are 28x28 pixels, and have one color channel
    input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

    # Convolutional Layer #1
    # Computes 32 features using a 5x5 filter with ReLU activation.
    # Padding is added to preserve width and height.
    # Input Tensor Shape: [batch_size, 28, 28, 1]
    # Output Tensor Shape: [batch_size, 28, 28, 32]
    conv1 = tf.layers.conv2d(
      inputs=input_layer,
      filters=32,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

    # Pooling Layer #1
    # First max pooling layer with a 2x2 filter and stride of 2
    # Input Tensor Shape: [batch_size, 28, 28, 32]
    # Output Tensor Shape: [batch_size, 14, 14, 32]
    pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

    # Convolutional Layer #2
    # Computes 64 features using a 5x5 filter.
    # Padding is added to preserve width and height.
    # Input Tensor Shape: [batch_size, 14, 14, 32]
    # Output Tensor Shape: [batch_size, 14, 14, 64]
    conv2 = tf.layers.conv2d(
      inputs=pool1,
      filters=64,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

    # Pooling Layer #2
    # Second max pooling layer with a 2x2 filter and stride of 2
    # Input Tensor Shape: [batch_size, 14, 14, 64]
    # Output Tensor Shape: [batch_size, 7, 7, 64]
    pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

    # Flatten tensor into a batch of vectors
    # Input Tensor Shape: [batch_size, 7, 7, 64]
    # Output Tensor Shape: [batch_size, 7 * 7 * 64]
    pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])

    # Dense Layer
    # Densely connected layer with 1024 neurons
    # Input Tensor Shape: [batch_size, 7 * 7 * 64]
    # Output Tensor Shape: [batch_size, 1024]
    dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)

    # Add dropout operation; 0.6 probability that element will be kept
    dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

    # Logits layer
    # Input Tensor Shape: [batch_size, 1024]
    # Output Tensor Shape: [batch_size, 10]
    logits = tf.layers.dense(inputs=dropout, units=10)

    predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
    }
    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

    # Calculate Loss (for both TRAIN and EVAL modes)
    loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

    # Configure the Training Op (for TRAIN mode)
    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
        train_op = optimizer.minimize(
            loss=loss,
            global_step=tf.train.get_global_step())
        return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

    # Add evaluation metrics (for EVAL mode)
    eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"])}
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

In [4]:
def main(unused_argv):
    # Load training and eval data
    mnist = tf.contrib.learn.datasets.load_dataset("mnist")
    train_data = mnist.train.images  # Returns np.array
    train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
    eval_data = mnist.test.images  # Returns np.array
    eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

    # Create the Estimator
    mnist_classifier = tf.estimator.Estimator(
      model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")

    # Set up logging for predictions
    # Log the values in the "Softmax" tensor with label "probabilities"
    tensors_to_log = {"probabilities": "softmax_tensor"}
    logging_hook = tf.train.LoggingTensorHook(
      tensors=tensors_to_log, every_n_iter=50)

    # Train the model
    train_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": train_data},
      y=train_labels,
      batch_size=100,
      num_epochs=None,
      shuffle=True)
    mnist_classifier.train(
      input_fn=train_input_fn,
      steps=20000,
      hooks=[logging_hook])

    # Evaluate the model and print results
    eval_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": eval_data},
      y=eval_labels,
      num_epochs=1,
      shuffle=False)
    eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
    print(eval_results)

In [5]:
if __name__ == "__main__":
  tf.app.run()

Successfully downloaded train-images-idx3-ubyte.gz 9912422 bytes.
Extracting MNIST-data/train-images-idx3-ubyte.gz
Successfully downloaded train-labels-idx1-ubyte.gz 28881 bytes.
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Successfully downloaded t10k-images-idx3-ubyte.gz 1648877 bytes.
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Successfully downloaded t10k-labels-idx1-ubyte.gz 4542 bytes.
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': '/tmp/mnist_convnet_model', '_tf_random_seed': 1, '_save_summary_steps': 100, '_save_checkpoints_secs': 600, '_save_checkpoints_steps': None, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000}
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model/model.ckpt-40000
INFO:tensorflow:Saving checkpoints for 40001 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:

INFO:tensorflow:probabilities = [[0.00000024 0.00000096 0.00023656 0.99878556 0.00000001 0.00015278
  0.00000001 0.         0.00081897 0.00000494]
 [0.00000225 0.01079636 0.9856113  0.00115703 0.00000016 0.00000053
  0.00000004 0.0000001  0.00243225 0.00000002]
 [0.9898218  0.00000726 0.00330288 0.00011894 0.00002205 0.00304018
  0.00003116 0.00156927 0.00004083 0.00204565]
 [0.00000048 0.00029504 0.99576676 0.00387197 0.00000001 0.00000073
  0.00000001 0.00002258 0.00004169 0.00000072]
 [0.00001322 0.9978934  0.00007869 0.0000485  0.00039385 0.00011644
  0.00027388 0.000165   0.00097181 0.00004512]
 [0.00000034 0.00002409 0.00007684 0.00105627 0.00002593 0.00000059
  0.00000002 0.9980768  0.00054962 0.00018944]
 [0.00000077 0.00000001 0.00000759 0.7436942  0.00000132 0.0211171
  0.00000001 0.00000689 0.20027867 0.03489338]
 [0.9998105  0.0000001  0.00001626 0.0000004  0.00000001 0.0001588
  0.00000116 0.0000089  0.00000007 0.00000384]
 [0.00000011 0.00000013 0.00004238 0.00000529 0.00

INFO:tensorflow:global_step/sec: 170.554
INFO:tensorflow:loss = 0.023908563, step = 40101 (0.587 sec)
INFO:tensorflow:probabilities = [[0.02209345 0.7528964  0.00719773 0.00248388 0.00013189 0.00013003
  0.00060666 0.00001717 0.21431266 0.00013007]
 [0.00069865 0.00447873 0.00215439 0.00397348 0.00040795 0.00041975
  0.00004583 0.00130869 0.9776414  0.00887108]
 [0.00002248 0.99532866 0.00043516 0.00009707 0.00011739 0.0000002
  0.00000057 0.00387583 0.00006397 0.00005876]
 [0.00000012 0.00000041 0.99992836 0.00006762 0.00000016 0.
  0.         0.00000022 0.00000303 0.00000008]
 [0.99898    0.00000132 0.00059557 0.00019749 0.00000106 0.00000683
  0.0000053  0.00000176 0.00016079 0.00004983]
 [0.000068   0.00014776 0.00058881 0.0000136  0.00040757 0.00014954
  0.9984994  0.00000057 0.00012466 0.00000013]
 [0.00000424 0.00000173 0.9999448  0.00000194 0.00000356 0.
  0.0000002  0.00000114 0.00004221 0.00000007]
 [0.00000129 0.99882954 0.00001041 0.00000099 0.00005165 0.00000042
  0.000000

INFO:tensorflow:probabilities = [[0.00008676 0.00000559 0.00110823 0.00023931 0.00000656 0.00001307
  0.00000001 0.97302496 0.00096953 0.02454589]
 [0.0000024  0.99981326 0.0000191  0.00003051 0.00001139 0.00000023
  0.00000109 0.00004468 0.00007576 0.00000154]
 [0.00000023 0.00000014 0.01211097 0.00001061 0.9874609  0.00007205
  0.00025538 0.00007708 0.00000015 0.00001246]
 [0.0000094  0.00000149 0.00000033 0.0000131  0.         0.99995625
  0.00001057 0.00000275 0.00000587 0.00000011]
 [0.00000219 0.00000004 0.0000001  0.00000005 0.00000046 0.00000196
  0.9999924  0.         0.00000287 0.00000001]
 [0.00000163 0.9998292  0.00000551 0.00000112 0.00004219 0.00000008
  0.00000027 0.00009752 0.00002183 0.00000058]
 [0.00000019 0.00000647 0.9999515  0.00002581 0.00001558 0.00000001
  0.00000008 0.0000002  0.00000013 0.00000003]
 [0.00005294 0.00000264 0.00058096 0.9989304  0.00000761 0.00025964
  0.00001455 0.00000063 0.0001391  0.00001154]
 [0.00000073 0.00000024 0.00000649 0.00000028 0.

INFO:tensorflow:global_step/sec: 187.792
INFO:tensorflow:loss = 0.06365141, step = 40201 (0.532 sec)
INFO:tensorflow:probabilities = [[0.9999908  0.0000037  0.0000012  0.00000007 0.         0.00000361
  0.00000039 0.00000003 0.00000008 0.00000016]
 [0.00000228 0.00001257 0.00002905 0.00000023 0.00001007 0.01697694
  0.9827418  0.         0.00022652 0.00000058]
 [0.00000134 0.00228763 0.00003028 0.00069021 0.89576155 0.00012088
  0.00001933 0.00011579 0.00006283 0.10091008]
 [0.00000064 0.000001   0.00024701 0.00000828 0.00000258 0.00000345
  0.99968493 0.00000003 0.0000521  0.00000003]
 [0.01228625 0.00020257 0.00176801 0.00430151 0.00569883 0.06223159
  0.00781935 0.89604896 0.00047394 0.00916897]
 [0.00001021 0.00002124 0.00008806 0.0048825  0.00605755 0.00000808
  0.00000007 0.00410462 0.00130205 0.98352563]
 [0.00000157 0.99982846 0.00004349 0.00000606 0.00000862 0.00000002
  0.00000038 0.00009946 0.00000904 0.00000295]
 [0.00000003 0.00000001 0.00000129 0.00000207 0.00000014 0.000

...

INFO:tensorflow:global_step/sec: 185.918
INFO:tensorflow:loss = 0.069348216, step = 59901 (0.538 sec)
INFO:tensorflow:probabilities = [[0.00000008 0.00000007 0.00000001 0.00000003 0.98163605 0.00000013
  0.00000001 0.00007225 0.00001932 0.01827199]
 [0.0000108  0.00000033 0.00000158 0.00000118 0.00015945 0.00000081
  0.00000001 0.99802315 0.00000201 0.00180071]
 [0.99835396 0.00000002 0.0000005  0.         0.00000422 0.00000021
  0.00163231 0.00000001 0.00000008 0.00000875]
 [0.00000046 0.00064575 0.00000001 0.00009109 0.00048183 0.00002189
  0.         0.00634785 0.00000062 0.99241054]
 [0.00038535 0.00008343 0.00208023 0.00473055 0.00002546 0.00370533
  0.00007204 0.00002281 0.96963274 0.01926205]
 [0.00000003 0.00000006 0.0000187  0.00004143 0.00000039 0.00000051
  0.00000018 0.00000001 0.99992526 0.00001347]
 [0.00000139 0.00014469 0.00000012 0.00000345 0.00000052 0.00000088
  0.         0.9956352  0.00000647 0.00420718]
 [0.00007059 0.00001034 0.00010482 0.00010464 0.0003436  0.00

INFO:tensorflow:probabilities = [[0.00000637 0.0000006  0.00000012 0.00032237 0.00048097 0.00010214
  0.00000002 0.09539591 0.00001043 0.90368104]
 [0.00001432 0.00000155 0.00000548 0.         0.00000333 0.00006144
  0.99976104 0.         0.00015281 0.00000003]
 [0.         0.00000006 0.00001158 0.9996562  0.         0.00031405
  0.         0.         0.00001773 0.0000004 ]
 [0.         0.00000005 0.99999774 0.00000204 0.00000007 0.
  0.         0.         0.0000001  0.        ]
 [0.00000191 0.00000057 0.00000176 0.00000161 0.00000105 0.00035525
  0.99961805 0.00000003 0.00001953 0.00000012]
 [0.         0.00000001 0.00000086 0.9999832  0.         0.0000001
  0.         0.00000001 0.00000111 0.00001473]
 [0.00017572 0.97583234 0.00070822 0.00332671 0.00386669 0.00156058
  0.00071379 0.00255906 0.00627989 0.00497708]
 [0.00000003 0.00000051 0.00000006 0.00003699 0.00013216 0.00000525
  0.         0.00001557 0.00000319 0.9998062 ]
 [0.         0.00000008 0.9999999  0.00000003 0.         

INFO:tensorflow:Saving checkpoints for 60000 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:Loss for final step: 0.0614887.
INFO:tensorflow:Starting evaluation at 2018-07-30-11:25:46
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model/model.ckpt-60000
INFO:tensorflow:Finished evaluation at 2018-07-30-11:25:46
INFO:tensorflow:Saving dict for global step 60000: accuracy = 0.9832, global_step = 60000, loss = 0.050934345
{'accuracy': 0.9832, 'loss': 0.050934345, 'global_step': 60000}


SystemExit: 

/home/hadas/.local/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2971: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)
